In [1]:
cd /Users/alessandropreviero/Desktop/vaccine-allocation/src

/Users/alessandropreviero/Desktop/vaccine-allocation/src


# Load saved solution

In [2]:
import pandas as pd
import datetime as dt
import numpy as np
import pickle
from pipeline.data_loading import load_and_clean_delphi_predictions
from models.prescriptive_delphi_model import DELPHISolution
import plotly.graph_objects as go

In [3]:
solution_dir = '/Users/alessandropreviero/Desktop/vaccine-allocation/data/outputs/optimized-solution-0.pickle'
delphi_dir = '/Users/alessandropreviero/Desktop/vaccine-allocation/data/inputs/delphi-predictions.csv'

In [4]:
with open(solution_dir, 'rb') as f:
    solution = pickle.load(f)

In [5]:
optimal_locations = solution.locations
infectious = solution.infectious
hospitalized_recovering = solution.hospitalized_recovering
quarantined_recovering = solution.quarantined_recovering
deceased = solution.deceased

# Plot DELPHI predicted deaths

In [18]:
delphi_pred_df = load_and_clean_delphi_predictions(delphi_dir)
deaths = delphi_pred_df[(delphi_pred_df.date >= dt.datetime(2021, 2, 1)) &
               (delphi_pred_df.date <= dt.datetime(2021, 4, 30))
              ][['date','recovered', 'state']]

In [19]:
first = deaths[deaths.date == dt.datetime(2021, 2, 1)]['recovered'].sum()
first

86220517.25561945

In [20]:
last = deaths[deaths.date == dt.datetime(2021, 4, 30)]['recovered'].sum()
last-first

35188315.3555406

In [14]:
import plotly.express as px
px.line(deaths, x='date', y='total_detected_deaths', color='state')

# Plot DELPHI active cases per state

In [8]:
cases = delphi_pred_df[(delphi_pred_df.date >= dt.datetime(2021, 2, 1)) &
               (delphi_pred_df.date <= dt.datetime(2021, 4, 30))
              ][['date','total_detected_cases', 'state']]

import plotly.express as px
px.line(cases, x='date', y='total_detected_cases', color='state')

# Plot active cases per state across time

In [78]:
active_cases = infectious + hospitalized_recovering + quarantined_recovering
active_cases = active_cases.sum(axis=1).T

In [79]:
states = pd.read_csv('/Users/alessandropreviero/Desktop/vaccine-allocation/data/inputs/county_pop_clean.csv')
states_names = states['state'].unique()

In [80]:
active_cases_df = pd.DataFrame(active_cases, columns=states_names)

In [81]:
active_plot = go.Figure()

for i in range(active_cases_df.shape[1]):
    active_plot.add_trace(
        go.Scatter(
            x=np.arange(91), 
            y=active_cases_df.iloc[:, i],
            mode='lines',
            name=active_cases_df.columns[i]
        )
    )
active_plot.update_layout(
    title="Active cases towards recovery by state"
)
active_plot.show()

# Plot cumulative deaths per state

In [82]:
deceased = solution.deceased.sum(axis=1).T
deceased_df = pd.DataFrame(deceased, columns=states_names)

In [83]:
deaths_plot = go.Figure()

for i in range(deceased_df.shape[1]):
    deaths_plot.add_trace(
        go.Scatter(
            x=np.arange(91), 
            y=deceased_df.iloc[:, i],
            mode='lines',
            name=deceased_df.columns[i]
        )
    )
deaths_plot.update_layout(
    title="Cumulative deaths towards recovery by state"
)
deaths_plot.show()

# Matching locations with states ordered by deaths

In [84]:
active_cases_flat = active_cases.flatten('F')

In [85]:
states = pd.read_csv('/Users/alessandropreviero/Desktop/vaccine-allocation/data/inputs/county_pop_clean.csv')
states_names = states['state'].unique()
repeated_arr = np.tile(states_names, 91)

In [86]:
long_df = pd.DataFrame({'states': repeated_arr, 'active_cases':active_cases_flat})
long_df['day'] = np.repeat(np.arange(91), 51)

In [87]:
locations_df = pd.DataFrame({'state': states_names, 'num_locations': optimal_locations})

In [89]:
deaths = solution.deceased[:,:,-1].sum(axis=1)
locations_df['deaths'] = deaths

In [91]:
locations_df.sort_values('state', ascending=True).head()

state  num_locations       deaths
0    AK            1.0   658.942085
1    AL            1.0    90.488301
2    AR            4.0  2061.923373
3    AZ            1.0   651.576435
4    CA            1.0  2536.138299

In [88]:
# long_df.to_csv('optimal_active_cases_map.csv')
# locations_df.to_csv('optimal_num_locations_states.csv')

### For Micheal if he wants to plot the map!

In [ ]:
deaths = solution.deceased[:,:,-1].sum(axis=1)
names = [us.states.lookup(x).name for x in states_names]

deaths_opt_df = pd.DataFrame(deaths, columns=['deaths'])
deaths_opt_df['state'] = names

In [ ]:
deaths_opt_df.head()